**To make the assignment, first run the code below to import the right libraries.**

In [2]:
# =================================
# Imports
# =================================
from PyCh import *
from numpy import random
from dataclasses import dataclass
from matplotlib import pyplot
import math

PyCh version 0.4 imported succesfully.
 


<h1><center> 4DC10. Intermediate assignment</center></h1>
<h2><center> Modeling and simulation of an autonomous vehicle storage and retrieval system</center></h2>
    
# 1 Subject

Today's competitive environment, in which deliveries need to be faster and order sizes become smaller, forces material handling providers to progressively develop new and better solutions. A recent development in automated material-handling technology for unit load storage and retrieval is the autonomous vehicle storage and retrieval system (AVS/RS). Figure 1 shows a representation of an AVS/RS for the handling of totes, while Figure 2 illustrates a single tier (floor, level). The storage racks are single-deep and double-sided. Each storage position is of the same size and can hold one tote. Lifts are mounted at fixed locations at one end of each storage aisle. The input/output (I/O) point is located at the first tier beside each lift. Autonomous vehicles are dedicated to a storage aisle within a specific tier (so-called tier-captive configuration). The first position on either side of the storage aisle in all tiers serves as a buffer and is used to manage the transfer of totes between vehicles and lifts (see Figure 2). One buffer (out) handles totes which have been retrieved, the other one (in), located on the other side of the storage aisle, handles the totes to be stored. The presence of these buffers allows the lift and vehicle to work independently of each other. 

The throughput performance of AVS/RS systems can be affected by design decisions (such as number of tiers, number of aisles, and depth of aisles) as well as operational decisions (such as tote storage location and order assignment).

Figure 1: AVS/RS with tier-captive configuration [1] | Figure 2: Single tier in AVS/RS [1]
- | - 
<img src="figures/avs.png" alt="drawing" width="400"/> | <img src="figures/avrs2.png" alt="drawing" width="400"/>




# 2 Goal
The goal of this assignment is to study this new material handling solution by using computer simulation. This study can be restricted to the retrieval process only, i.e., the vehicles perform only single retrieval cycles. Clearly, the retrieval phase is the most critical activity from an organisational viewpoint, as it is directly related to customer service level and &mdash; in contrast to the storage phase &mdash; it cannot be postponed to a period of low workload. 

The objectives of this assignment can be summarized as follows:
- Develop a simulation model of one aisle that consists of Level tiers with retrieval process to assess the system performance in terms of throughput and flow time.
- Systematically develop the model process by process, and verify and validate each process using analytical results.
- Investigate design trade-offs, i.e., via different layouts (number of columns and tiers), for this material handling system.

# 3 Description of the AVS/RS
The AVS/RS is a fully automated system that can store and retrieve unit loads. The unit loads are placed in totes, a type of box, and these totes are placed in a designated aisle and column for storage. When retrieved, an autonomous vehicle places the totes in a buffer at the end of the aisle. There is one autonomous vehicle for every aisle within the tier. This is called the tier-captive configuration. From the buffer, the totes are picked by a lift that serves all tiers inone aisle, see Figure 2. In this assignment only one aisle that consists of `Level` tiers has to be modelled. Each aisle has depth number of columns of width `dv` metres and height `dl` metres.

Requests for a tote arrive for each tier, asking for a tote with a random (uniformly distributed) column assigned to it. The inter arrival time of requests is exponentially distributed with mean value `arrive`.

The vehicles transport totes along the aisle (one vehicle per tier). The time taken by the vehicle to process an order depends on the tote's location. The vehicle has to travel to this location, load the tote (it takes a fixed amount of time equal to `lv` seconds), then go back to the end of the aisle and, finally, unload the tote to the buffer (again this takes `lv` seconds). The speed profile of each vehicle is described as follows. First, the vehicle goes with a constant acceleration `av` *m/s$^2$* until it reaches its maximum velocity `vmaxv`, then it moves with this velocity and decelerates with a constant deceleration `av` to approach its destination point. If the tote is located too close to the end of the aisle, it is possible that the vehicle will not reach its maximum speed.

The vehicles unload the totes to a location where it is picked up by the lift. At any given time only one tote per tier is allowed to occupy such a position.

The lift transports the totes from every tier to the ground floor. The processing time depends on the tote's location and the fixed time to load and unload the tote (`ll` seconds for loading and `ll` seconds for unloading). The maximum speed of the lift is `vmaxl` *m/s* with a speed profile similar to that of the vehicles (constant acceleration/deceleration of `al` *m/s<sup>2</sup>*).

# 4 Modeling of the AVS/RS
The model consists of several processes communicating via channels, see Figure 3.

| Figure 3: The processes in the model | 
- 
<img src="figures/avrs.png" alt="drawing" width="400"/> 

A brief description of the processes is given below:
- **G:** The generator models the arrival of orders for totes. There is one generator per tier.
- **DB:** The demand buffer stores the orders to be picked up by the vehicles. The vehicle processes the orders under first-come-first-serve policy. It can always receive a tote, but it releases a tote only when the vehicle is ready to pick it up.
- **V:** The vehicle can be modeled as a server with a variable processing time.
- **GDV:** The process consisting of a Generator, Demand Buffer and Vehicle for one tier of the AVS/RS system.
- **B:** The buffer stores the totes from the vehicles awaiting for a pick-up by the lift. The buffer operates under first-come-first-serve policy and has a finite capacity of `bc` totes per tier. So, every tier has a buffer location of finite capacity of `bc` totes. All those locations together form the buffer B that accommodates all the totes which are processed by the same lift. When the buffer is not empty (there is at least one tote on one of the tiers), the buffer sends information about the tier of the longest waiting tote to the lift upon request. This information is used by the lift to determine the location of the tote (the number of the tier the tote is located in). Once the lift is ready to pick it up, the tote is released to the lift. There are two types of queues in the buffer: `xs` contains all the totes to be picked up by the lift and there are Level counters `n` counting the totes from the corresponding tier.
- **L:** The lift, similar to the process V, is modeled as a machine with a variable processing time. A lift first receives a destination tier. Then the process delays for time required for the lift to go to the tote location and pick up the tote. Then it receives the tote, and next it delays for the time required to go to the ground floor and to unload the tote. After that the lift process is ready to release the tote to the Exit process.
- **E:** In the exit process all the data related to each tote are collected. This process calculates the average throughput and the average flow-time. The number of totes to be processed by the AVS/RS during one simulation run is determined by the constant `Number_of_orders`.

# 5 Remark concerning report
All questions must be answered in this file (with the exeception of the lot-time diagrams, which must be attached as seperate files). Avoid unnecessary long explanations, however answers to analytical questions without an argument will result in no points. You can add extra Cells to add code or text (markdown) to the notebook. Markdown (text) boxes support Latex for writing formulas, e.g. `$ y = a \cdot x^2 $` turns into $ y = a \cdot x^2 $. More info: [Markdown](https://personal.math.ubc.ca/~pwalls/math-python/jupyter/markdown/) and [Latex](https://personal.math.ubc.ca/~pwalls/math-python/jupyter/latex/).

Both the notebook, and a PDF of the notebook must be submitted. To download the notebook file: click `File` > `Download as` > `Notebook (.ipynb)`. To download a PDF: press `Control + P` and `Save as PDF` (do not use the Jupyter Print options, as they will print the entire output of your simulations).

# 6 Assignment
When making a SimPy specification, one does not build an entire model and then starts debugging. A model is build step by step. During each step proper functionality is checked. We therefore model one process at a time, and connect the process with a Generator and/or Exit process to test proper functionality. In order to test proper functionality we first use analytical methods to determine the expected outcome. Then we run simulations to verify if these outcomes are indeed obtained. If that is the case, we can be more convinced that the process has been modeled correctly.


## 6.1 Exercise 1: Generator (5 points)
So the first step is to write a proper generator for a tier. To that end, the first model we build consists of (only) a Generator process and an Exit process collecting the totes generated by the Generator. The inter arrival time of requests is exponentially distributed with mean `arrive`. The requested tote should be retrieved from a random (uniformly distributed) column, where there are `depth` columns in total.

a. Determine (analytically) the throughput and flow time that should result from your model with only the generator process and the exit process.

Answer: ...



b. Complete the simulation code from the following template:

In [3]:
# =================================
# Global
# =================================
arrive = 70.0             # inter arrival time of requests
depth  = 55               # the number of columns
number_of_orders = 10000  # the number of orders to process

# =================================
# Tote
# =================================
@dataclass
class Tote:
    entrytime: float = 0.0
    column: int = 0

# =================================
# Generator
# =================================
@process
def Generator(env, c_out):
    ### BEGIN SOLUTION
    ta_dist = lambda: random.exponential(arrive)
    column_dist = lambda:  random.randint(0, depth)
    ### END SOLUTION
    x = Tote()
    while True:
        x.entrytime = env.now
        # x.column = ..... 
        ### BEGIN SOLUTION
        x.column = column_dist()
        ### END SOLUTION
        yield env.execute(c_out.send(x))
        # delay = ..... 
        ### BEGIN SOLUTION
        delay = ta_dist()
        ### END SOLUTION
        yield env.timeout(delay)


# =================================
# Exit
# =================================
@process
def Exit(env, c_in):
    x = Tote()
    mphi = 0
    for i in range(1, number_of_orders + 1):
        x = yield env.execute(c_in.receive())
        mphi = (i - 1) / i * mphi + (env.now - x.entrytime) / i
        print(f"tote = {i:6d};"  
              f"  Entrytime = {x.entrytime: 10.4f};" 
              f"  Column = {x.column:2d};"
              f"  Mean throughput =" + (f"{i / env.now:8.6f}"   if   env.now   else f"{'N.A.':>8s}") +
              f"  Mean flowtime = {mphi:6.4f}" 
        )


# =================================
# Model
# =================================
def model():
    env = Environment()
    a = Channel(env)
    G = Generator(env, a)
    E = Exit(env, a)
    env.run(until=E)
    print ("simulation has ended")

# =================================
# Main
# =================================
model()


tote =      1;  Entrytime =     0.0000;  Column = 27;  Mean throughput =    N.A.  Mean flowtime = 0.0000
tote =      2;  Entrytime =    86.8470;  Column = 16;  Mean throughput =0.023029  Mean flowtime = 0.0000
tote =      3;  Entrytime =   224.4893;  Column = 17;  Mean throughput =0.013364  Mean flowtime = 0.0000
tote =      4;  Entrytime =   324.6917;  Column = 52;  Mean throughput =0.012319  Mean flowtime = 0.0000
tote =      5;  Entrytime =   358.0906;  Column = 40;  Mean throughput =0.013963  Mean flowtime = 0.0000
tote =      6;  Entrytime =   401.1544;  Column = 36;  Mean throughput =0.014957  Mean flowtime = 0.0000
tote =      7;  Entrytime =   410.4458;  Column = 51;  Mean throughput =0.017055  Mean flowtime = 0.0000
tote =      8;  Entrytime =   437.8372;  Column =  1;  Mean throughput =0.018272  Mean flowtime = 0.0000
tote =      9;  Entrytime =   457.9932;  Column = 29;  Mean throughput =0.019651  Mean flowtime = 0.0000
tote =     10;  Entrytime =   486.0274;  Column =  0;  

tote =    187;  Entrytime =  12263.3147;  Column = 18;  Mean throughput =0.015249  Mean flowtime = 0.0000
tote =    188;  Entrytime =  12292.0525;  Column = 46;  Mean throughput =0.015294  Mean flowtime = 0.0000
tote =    189;  Entrytime =  12317.6046;  Column = 30;  Mean throughput =0.015344  Mean flowtime = 0.0000
tote =    190;  Entrytime =  12384.5754;  Column =  8;  Mean throughput =0.015342  Mean flowtime = 0.0000
tote =    191;  Entrytime =  12469.0236;  Column =  1;  Mean throughput =0.015318  Mean flowtime = 0.0000
tote =    192;  Entrytime =  12587.9138;  Column = 10;  Mean throughput =0.015253  Mean flowtime = 0.0000
tote =    193;  Entrytime =  12627.7955;  Column = 25;  Mean throughput =0.015284  Mean flowtime = 0.0000
tote =    194;  Entrytime =  12628.8314;  Column = 35;  Mean throughput =0.015362  Mean flowtime = 0.0000
tote =    195;  Entrytime =  12698.8852;  Column = 27;  Mean throughput =0.015356  Mean flowtime = 0.0000
tote =    196;  Entrytime =  12869.9417;  Colu

tote =    670;  Entrytime =  45505.7836;  Column = 48;  Mean throughput =0.014723  Mean flowtime = 0.0000
tote =    671;  Entrytime =  45548.0393;  Column = 48;  Mean throughput =0.014732  Mean flowtime = 0.0000
tote =    672;  Entrytime =  45680.8379;  Column = 37;  Mean throughput =0.014711  Mean flowtime = 0.0000
tote =    673;  Entrytime =  45683.4582;  Column = 17;  Mean throughput =0.014732  Mean flowtime = 0.0000
tote =    674;  Entrytime =  45723.8572;  Column = 20;  Mean throughput =0.014741  Mean flowtime = 0.0000
tote =    675;  Entrytime =  45743.1868;  Column = 53;  Mean throughput =0.014756  Mean flowtime = 0.0000
tote =    676;  Entrytime =  45782.8088;  Column = 20;  Mean throughput =0.014765  Mean flowtime = 0.0000
tote =    677;  Entrytime =  45791.7654;  Column = 11;  Mean throughput =0.014784  Mean flowtime = 0.0000
tote =    678;  Entrytime =  46041.7364;  Column = 34;  Mean throughput =0.014726  Mean flowtime = 0.0000
tote =    679;  Entrytime =  46085.4525;  Colu

tote =    970;  Entrytime =  65499.6509;  Column = 34;  Mean throughput =0.014809  Mean flowtime = 0.0000
tote =    971;  Entrytime =  65519.9892;  Column = 25;  Mean throughput =0.014820  Mean flowtime = 0.0000
tote =    972;  Entrytime =  65521.4742;  Column = 46;  Mean throughput =0.014835  Mean flowtime = 0.0000
tote =    973;  Entrytime =  65542.7627;  Column = 54;  Mean throughput =0.014845  Mean flowtime = 0.0000
tote =    974;  Entrytime =  65705.4296;  Column = 44;  Mean throughput =0.014824  Mean flowtime = 0.0000
tote =    975;  Entrytime =  66105.2650;  Column = 20;  Mean throughput =0.014749  Mean flowtime = 0.0000
tote =    976;  Entrytime =  66161.1935;  Column = 31;  Mean throughput =0.014752  Mean flowtime = 0.0000
tote =    977;  Entrytime =  66247.2265;  Column = 39;  Mean throughput =0.014748  Mean flowtime = 0.0000
tote =    978;  Entrytime =  66360.5743;  Column =  2;  Mean throughput =0.014738  Mean flowtime = 0.0000
tote =    979;  Entrytime =  66480.5800;  Colu

tote =   1189;  Entrytime =  80687.7112;  Column =  8;  Mean throughput =0.014736  Mean flowtime = 0.0000
tote =   1190;  Entrytime =  80789.3873;  Column = 50;  Mean throughput =0.014730  Mean flowtime = 0.0000
tote =   1191;  Entrytime =  80852.6203;  Column = 37;  Mean throughput =0.014731  Mean flowtime = 0.0000
tote =   1192;  Entrytime =  80900.9077;  Column = 36;  Mean throughput =0.014734  Mean flowtime = 0.0000
tote =   1193;  Entrytime =  80903.4604;  Column = 52;  Mean throughput =0.014746  Mean flowtime = 0.0000
tote =   1194;  Entrytime =  81030.4087;  Column = 20;  Mean throughput =0.014735  Mean flowtime = 0.0000
tote =   1195;  Entrytime =  81083.9268;  Column = 47;  Mean throughput =0.014738  Mean flowtime = 0.0000
tote =   1196;  Entrytime =  81216.2966;  Column =  8;  Mean throughput =0.014726  Mean flowtime = 0.0000
tote =   1197;  Entrytime =  81235.5593;  Column = 54;  Mean throughput =0.014735  Mean flowtime = 0.0000
tote =   1198;  Entrytime =  81247.3174;  Colu

...

tote =   7963;  Entrytime =  543900.0836;  Column = 48;  Mean throughput =0.014641  Mean flowtime = 0.0000
tote =   7964;  Entrytime =  543952.2090;  Column = 22;  Mean throughput =0.014641  Mean flowtime = 0.0000
tote =   7965;  Entrytime =  543980.7629;  Column = 14;  Mean throughput =0.014642  Mean flowtime = 0.0000
tote =   7966;  Entrytime =  544051.3355;  Column = 44;  Mean throughput =0.014642  Mean flowtime = 0.0000
tote =   7967;  Entrytime =  544304.2752;  Column = 31;  Mean throughput =0.014637  Mean flowtime = 0.0000
tote =   7968;  Entrytime =  544312.5142;  Column = 20;  Mean throughput =0.014639  Mean flowtime = 0.0000
tote =   7969;  Entrytime =  544519.8343;  Column = 13;  Mean throughput =0.014635  Mean flowtime = 0.0000
tote =   7970;  Entrytime =  544523.3120;  Column = 50;  Mean throughput =0.014637  Mean flowtime = 0.0000
tote =   7971;  Entrytime =  544594.5607;  Column = 28;  Mean throughput =0.014637  Mean flowtime = 0.0000
tote =   7972;  Entrytime =  544667.8

tote =   8462;  Entrytime =  578288.0520;  Column = 52;  Mean throughput =0.014633  Mean flowtime = 0.0000
tote =   8463;  Entrytime =  578292.6366;  Column = 36;  Mean throughput =0.014634  Mean flowtime = 0.0000
tote =   8464;  Entrytime =  578356.7945;  Column = 47;  Mean throughput =0.014635  Mean flowtime = 0.0000
tote =   8465;  Entrytime =  578386.6505;  Column = 28;  Mean throughput =0.014636  Mean flowtime = 0.0000
tote =   8466;  Entrytime =  578469.4462;  Column = 51;  Mean throughput =0.014635  Mean flowtime = 0.0000
tote =   8467;  Entrytime =  578558.2918;  Column =  1;  Mean throughput =0.014635  Mean flowtime = 0.0000
tote =   8468;  Entrytime =  578750.4642;  Column = 33;  Mean throughput =0.014632  Mean flowtime = 0.0000
tote =   8469;  Entrytime =  578927.8263;  Column = 33;  Mean throughput =0.014629  Mean flowtime = 0.0000
tote =   8470;  Entrytime =  578974.0735;  Column =  6;  Mean throughput =0.014629  Mean flowtime = 0.0000
tote =   8471;  Entrytime =  579006.1

tote =   8962;  Entrytime =  612660.0910;  Column = 17;  Mean throughput =0.014628  Mean flowtime = 0.0000
tote =   8963;  Entrytime =  612755.5398;  Column = 32;  Mean throughput =0.014627  Mean flowtime = 0.0000
tote =   8964;  Entrytime =  612770.7902;  Column = 29;  Mean throughput =0.014629  Mean flowtime = 0.0000
tote =   8965;  Entrytime =  612866.8898;  Column = 18;  Mean throughput =0.014628  Mean flowtime = 0.0000
tote =   8966;  Entrytime =  612874.6973;  Column = 23;  Mean throughput =0.014629  Mean flowtime = 0.0000
tote =   8967;  Entrytime =  612903.4612;  Column = 14;  Mean throughput =0.014630  Mean flowtime = 0.0000
tote =   8968;  Entrytime =  612906.7332;  Column = 21;  Mean throughput =0.014632  Mean flowtime = 0.0000
tote =   8969;  Entrytime =  613071.1986;  Column = 34;  Mean throughput =0.014630  Mean flowtime = 0.0000
tote =   8970;  Entrytime =  613076.8628;  Column = 29;  Mean throughput =0.014631  Mean flowtime = 0.0000
tote =   8971;  Entrytime =  613093.2

tote =   9461;  Entrytime =  646087.5157;  Column = 52;  Mean throughput =0.014644  Mean flowtime = 0.0000
tote =   9462;  Entrytime =  646397.1100;  Column =  4;  Mean throughput =0.014638  Mean flowtime = 0.0000
tote =   9463;  Entrytime =  646421.3825;  Column = 43;  Mean throughput =0.014639  Mean flowtime = 0.0000
tote =   9464;  Entrytime =  646422.4599;  Column = 15;  Mean throughput =0.014641  Mean flowtime = 0.0000
tote =   9465;  Entrytime =  646455.7883;  Column = 33;  Mean throughput =0.014641  Mean flowtime = 0.0000
tote =   9466;  Entrytime =  646736.5156;  Column = 52;  Mean throughput =0.014637  Mean flowtime = 0.0000
tote =   9467;  Entrytime =  646819.0180;  Column =  9;  Mean throughput =0.014636  Mean flowtime = 0.0000
tote =   9468;  Entrytime =  646847.2948;  Column = 29;  Mean throughput =0.014637  Mean flowtime = 0.0000
tote =   9469;  Entrytime =  646853.5987;  Column =  8;  Mean throughput =0.014639  Mean flowtime = 0.0000
tote =   9470;  Entrytime =  646873.0

tote =   9961;  Entrytime =  681740.5813;  Column = 11;  Mean throughput =0.014611  Mean flowtime = 0.0000
tote =   9962;  Entrytime =  681818.3773;  Column = 26;  Mean throughput =0.014611  Mean flowtime = 0.0000
tote =   9963;  Entrytime =  681870.7469;  Column = 30;  Mean throughput =0.014611  Mean flowtime = 0.0000
tote =   9964;  Entrytime =  681943.1142;  Column = 43;  Mean throughput =0.014611  Mean flowtime = 0.0000
tote =   9965;  Entrytime =  681983.5152;  Column = 18;  Mean throughput =0.014612  Mean flowtime = 0.0000
tote =   9966;  Entrytime =  682033.0495;  Column = 37;  Mean throughput =0.014612  Mean flowtime = 0.0000
tote =   9967;  Entrytime =  682171.1762;  Column = 52;  Mean throughput =0.014611  Mean flowtime = 0.0000
tote =   9968;  Entrytime =  682185.6646;  Column =  4;  Mean throughput =0.014612  Mean flowtime = 0.0000
tote =   9969;  Entrytime =  682186.1722;  Column = 47;  Mean throughput =0.014613  Mean flowtime = 0.0000
tote =   9970;  Entrytime =  682235.2

c. Confirm that your simulations produce the correct throughput and flow time. Also determine the minimal and maximal column returned by your simulation.

Answer: ...



Run your simulation at least 10 times. What is the range of outcomes for the mean throughput? Determine (roughly, by trial and error) the number of orders required to get good estimates for the throughput (first three non-zero digits are correct).

## 6.2 Exercise 2: Demand Buffer (5 points)
Next, we include the Demand buffer which is modelled as a standard FIFO buffer with infinite capacity.

a. Determine (analytically) the throughput and flow time that should result from your model with only the generator process, demand buffer, and the exit process.

Answer: ...



b. Complete the simulation code in the template below.

Note: The previously defined variables and functions remain unchanged, only the Demand Buffer is added, and the main code is changed.

In [4]:
# =================================
# Demand Buffer
# =================================
@process
def Demand_Buffer(env, c_in, c_out):
    xs = [] # list of totes
    while True:
            ### BEGIN SOLUTION
            receiving = c_in.receive() 
            sending = c_out.send(xs[0]) if len(xs)>0 else None
            yield env.select(sending,receiving)
            if selected(sending):
                xs = xs[1:]
            if selected(receiving):
                x = receiving.entity
                xs = xs + [x]
            ### END SOLUTION

# =================================
# Model
# =================================
def model():
    env = Environment()
    a = Channel(env)
    b = Channel(env)
    G = Generator(env, a)
    D = Demand_Buffer(env, a,b)
    E = Exit(env, b)
    env.run(until=E)
    print ("simulation has ended")
    
# =================================
# Main
# =================================
model()

tote =      1;  Entrytime =     0.0000;  Column =  5;  Mean throughput =    N.A.  Mean flowtime = 0.0000
tote =      2;  Entrytime =     3.7636;  Column = 13;  Mean throughput =0.531408  Mean flowtime = 0.0000
tote =      3;  Entrytime =   219.4312;  Column = 49;  Mean throughput =0.013672  Mean flowtime = 0.0000
tote =      4;  Entrytime =   222.5231;  Column = 41;  Mean throughput =0.017976  Mean flowtime = 0.0000
tote =      5;  Entrytime =   222.7033;  Column = 54;  Mean throughput =0.022451  Mean flowtime = 0.0000
tote =      6;  Entrytime =   281.9313;  Column = 50;  Mean throughput =0.021282  Mean flowtime = 0.0000
tote =      7;  Entrytime =   297.5376;  Column = 33;  Mean throughput =0.023526  Mean flowtime = 0.0000
tote =      8;  Entrytime =   298.9247;  Column = 15;  Mean throughput =0.026763  Mean flowtime = 0.0000
tote =      9;  Entrytime =   429.1171;  Column = 40;  Mean throughput =0.020973  Mean flowtime = 0.0000
tote =     10;  Entrytime =   512.6612;  Column = 11;  

tote =    273;  Entrytime =  18459.2076;  Column = 43;  Mean throughput =0.014789  Mean flowtime = 0.0000
tote =    274;  Entrytime =  18460.1921;  Column = 28;  Mean throughput =0.014843  Mean flowtime = 0.0000
tote =    275;  Entrytime =  18540.5643;  Column =  6;  Mean throughput =0.014832  Mean flowtime = 0.0000
tote =    276;  Entrytime =  18597.7652;  Column = 49;  Mean throughput =0.014840  Mean flowtime = 0.0000
tote =    277;  Entrytime =  18604.4585;  Column = 26;  Mean throughput =0.014889  Mean flowtime = 0.0000
tote =    278;  Entrytime =  18638.9879;  Column = 14;  Mean throughput =0.014915  Mean flowtime = 0.0000
tote =    279;  Entrytime =  18662.7039;  Column = 11;  Mean throughput =0.014950  Mean flowtime = 0.0000
tote =    280;  Entrytime =  18766.5513;  Column = 11;  Mean throughput =0.014920  Mean flowtime = 0.0000
tote =    281;  Entrytime =  18861.7764;  Column = 20;  Mean throughput =0.014898  Mean flowtime = 0.0000
tote =    282;  Entrytime =  18878.3398;  Colu

tote =    453;  Entrytime =  29226.4677;  Column =  7;  Mean throughput =0.015500  Mean flowtime = 0.0000
tote =    454;  Entrytime =  29280.1668;  Column = 11;  Mean throughput =0.015505  Mean flowtime = 0.0000
tote =    455;  Entrytime =  29283.6488;  Column =  4;  Mean throughput =0.015538  Mean flowtime = 0.0000
tote =    456;  Entrytime =  29290.9268;  Column =  2;  Mean throughput =0.015568  Mean flowtime = 0.0000
tote =    457;  Entrytime =  29357.8771;  Column = 12;  Mean throughput =0.015567  Mean flowtime = 0.0000
tote =    458;  Entrytime =  29409.8916;  Column = 10;  Mean throughput =0.015573  Mean flowtime = 0.0000
tote =    459;  Entrytime =  29411.4641;  Column = 51;  Mean throughput =0.015606  Mean flowtime = 0.0000
tote =    460;  Entrytime =  29566.5267;  Column = 30;  Mean throughput =0.015558  Mean flowtime = 0.0000
tote =    461;  Entrytime =  29650.9874;  Column = 32;  Mean throughput =0.015548  Mean flowtime = 0.0000
tote =    462;  Entrytime =  29725.7926;  Colu

tote =    678;  Entrytime =  46592.8838;  Column = 42;  Mean throughput =0.014552  Mean flowtime = 0.0000
tote =    679;  Entrytime =  46605.2249;  Column = 13;  Mean throughput =0.014569  Mean flowtime = 0.0000
tote =    680;  Entrytime =  46703.0975;  Column = 15;  Mean throughput =0.014560  Mean flowtime = 0.0000
tote =    681;  Entrytime =  46704.5988;  Column =  3;  Mean throughput =0.014581  Mean flowtime = 0.0000
tote =    682;  Entrytime =  46746.0324;  Column = 32;  Mean throughput =0.014589  Mean flowtime = 0.0000
tote =    683;  Entrytime =  46762.1944;  Column = 10;  Mean throughput =0.014606  Mean flowtime = 0.0000
tote =    684;  Entrytime =  46868.1969;  Column = 10;  Mean throughput =0.014594  Mean flowtime = 0.0000
tote =    685;  Entrytime =  46901.1806;  Column = 21;  Mean throughput =0.014605  Mean flowtime = 0.0000
tote =    686;  Entrytime =  47118.6140;  Column = 54;  Mean throughput =0.014559  Mean flowtime = 0.0000
tote =    687;  Entrytime =  47136.0242;  Colu

tote =    952;  Entrytime =  65278.0022;  Column =  7;  Mean throughput =0.014584  Mean flowtime = 0.0000
tote =    953;  Entrytime =  65445.1416;  Column = 24;  Mean throughput =0.014562  Mean flowtime = 0.0000
tote =    954;  Entrytime =  65643.7307;  Column = 50;  Mean throughput =0.014533  Mean flowtime = 0.0000
tote =    955;  Entrytime =  65697.6417;  Column = 42;  Mean throughput =0.014536  Mean flowtime = 0.0000
tote =    956;  Entrytime =  65725.7722;  Column = 41;  Mean throughput =0.014545  Mean flowtime = 0.0000
tote =    957;  Entrytime =  65905.7611;  Column = 15;  Mean throughput =0.014521  Mean flowtime = 0.0000
tote =    958;  Entrytime =  66011.5612;  Column = 50;  Mean throughput =0.014513  Mean flowtime = 0.0000
tote =    959;  Entrytime =  66082.5949;  Column = 12;  Mean throughput =0.014512  Mean flowtime = 0.0000
tote =    960;  Entrytime =  66098.6033;  Column = 10;  Mean throughput =0.014524  Mean flowtime = 0.0000
tote =    961;  Entrytime =  66184.1187;  Colu

...

tote =   7445;  Entrytime =  518065.7235;  Column = 28;  Mean throughput =0.014371  Mean flowtime = 0.0000
tote =   7446;  Entrytime =  518261.0246;  Column = 41;  Mean throughput =0.014367  Mean flowtime = 0.0000
tote =   7447;  Entrytime =  518334.7433;  Column = 26;  Mean throughput =0.014367  Mean flowtime = 0.0000
tote =   7448;  Entrytime =  518355.6345;  Column = 54;  Mean throughput =0.014369  Mean flowtime = 0.0000
tote =   7449;  Entrytime =  518454.7337;  Column = 27;  Mean throughput =0.014368  Mean flowtime = 0.0000
tote =   7450;  Entrytime =  518484.3358;  Column = 40;  Mean throughput =0.014369  Mean flowtime = 0.0000
tote =   7451;  Entrytime =  518560.5248;  Column = 18;  Mean throughput =0.014369  Mean flowtime = 0.0000
tote =   7452;  Entrytime =  518646.1916;  Column = 32;  Mean throughput =0.014368  Mean flowtime = 0.0000
tote =   7453;  Entrytime =  518651.9812;  Column = 28;  Mean throughput =0.014370  Mean flowtime = 0.0000
tote =   7454;  Entrytime =  518668.1

tote =   7945;  Entrytime =  552867.5786;  Column = 12;  Mean throughput =0.014371  Mean flowtime = 0.0000
tote =   7946;  Entrytime =  552877.2615;  Column = 35;  Mean throughput =0.014372  Mean flowtime = 0.0000
tote =   7947;  Entrytime =  552944.2794;  Column =  6;  Mean throughput =0.014372  Mean flowtime = 0.0000
tote =   7948;  Entrytime =  553001.1764;  Column = 53;  Mean throughput =0.014372  Mean flowtime = 0.0000
tote =   7949;  Entrytime =  553004.4457;  Column = 44;  Mean throughput =0.014374  Mean flowtime = 0.0000
tote =   7950;  Entrytime =  553048.6332;  Column = 29;  Mean throughput =0.014375  Mean flowtime = 0.0000
tote =   7951;  Entrytime =  553066.6953;  Column =  5;  Mean throughput =0.014376  Mean flowtime = 0.0000
tote =   7952;  Entrytime =  553362.1161;  Column = 27;  Mean throughput =0.014370  Mean flowtime = 0.0000
tote =   7953;  Entrytime =  553394.9031;  Column = 21;  Mean throughput =0.014371  Mean flowtime = 0.0000
tote =   7954;  Entrytime =  553404.8

tote =   8444;  Entrytime =  586955.8876;  Column =  0;  Mean throughput =0.014386  Mean flowtime = 0.0000
tote =   8445;  Entrytime =  586961.9312;  Column = 42;  Mean throughput =0.014388  Mean flowtime = 0.0000
tote =   8446;  Entrytime =  586995.2163;  Column = 31;  Mean throughput =0.014389  Mean flowtime = 0.0000
tote =   8447;  Entrytime =  586996.0133;  Column =  1;  Mean throughput =0.014390  Mean flowtime = 0.0000
tote =   8448;  Entrytime =  587012.8171;  Column = 23;  Mean throughput =0.014392  Mean flowtime = 0.0000
tote =   8449;  Entrytime =  587093.0596;  Column = 43;  Mean throughput =0.014391  Mean flowtime = 0.0000
tote =   8450;  Entrytime =  587140.4697;  Column = 35;  Mean throughput =0.014392  Mean flowtime = 0.0000
tote =   8451;  Entrytime =  587165.1426;  Column =  6;  Mean throughput =0.014393  Mean flowtime = 0.0000
tote =   8452;  Entrytime =  587206.0023;  Column =  8;  Mean throughput =0.014394  Mean flowtime = 0.0000
tote =   8453;  Entrytime =  587289.3

tote =   9331;  Entrytime =  645145.0091;  Column = 53;  Mean throughput =0.014463  Mean flowtime = 0.0000
tote =   9332;  Entrytime =  645202.1650;  Column = 15;  Mean throughput =0.014464  Mean flowtime = 0.0000
tote =   9333;  Entrytime =  645301.5077;  Column = 27;  Mean throughput =0.014463  Mean flowtime = 0.0000
tote =   9334;  Entrytime =  645360.0716;  Column = 12;  Mean throughput =0.014463  Mean flowtime = 0.0000
tote =   9335;  Entrytime =  645471.7082;  Column =  3;  Mean throughput =0.014462  Mean flowtime = 0.0000
tote =   9336;  Entrytime =  645520.6492;  Column =  7;  Mean throughput =0.014463  Mean flowtime = 0.0000
tote =   9337;  Entrytime =  645522.3749;  Column = 35;  Mean throughput =0.014464  Mean flowtime = 0.0000
tote =   9338;  Entrytime =  645606.4068;  Column = 44;  Mean throughput =0.014464  Mean flowtime = 0.0000
tote =   9339;  Entrytime =  645613.0558;  Column =  6;  Mean throughput =0.014465  Mean flowtime = 0.0000
tote =   9340;  Entrytime =  645628.5

tote =   9943;  Entrytime =  688690.9843;  Column = 38;  Mean throughput =0.014438  Mean flowtime = 0.0000
tote =   9944;  Entrytime =  688722.5730;  Column = 25;  Mean throughput =0.014438  Mean flowtime = 0.0000
tote =   9945;  Entrytime =  688839.6837;  Column = 20;  Mean throughput =0.014437  Mean flowtime = 0.0000
tote =   9946;  Entrytime =  688985.9537;  Column = 19;  Mean throughput =0.014436  Mean flowtime = 0.0000
tote =   9947;  Entrytime =  689062.1011;  Column = 51;  Mean throughput =0.014436  Mean flowtime = 0.0000
tote =   9948;  Entrytime =  689077.9921;  Column = 47;  Mean throughput =0.014437  Mean flowtime = 0.0000
tote =   9949;  Entrytime =  689168.9161;  Column = 51;  Mean throughput =0.014436  Mean flowtime = 0.0000
tote =   9950;  Entrytime =  689226.7347;  Column = 14;  Mean throughput =0.014436  Mean flowtime = 0.0000
tote =   9951;  Entrytime =  689389.3145;  Column = 40;  Mean throughput =0.014435  Mean flowtime = 0.0000
tote =   9952;  Entrytime =  689426.0

c. Confirm that your simulations produce the correct throughput and flow time.

Answer: ...



## 6.3 Exercise 3: Vehicle as machine (5 points)
Next, we include the Vehicle which as a first attempt is modelled as a standard machine with a deterministic processing time of 40.0 seconds

a. Determine (analytically) the throughput and flow time that should result from your model with only the generator process, demand buffer, vehicle and the exit process.

Answer: ...



b. Complete the simulation code in the template below.

Note: The previously defined variables and functions remain unchanged, only the Vehicle is added, and the main code is changed.

In [5]:
# =================================
# Vehicle
# =================================
@process
def Vehicle(env, c_in, c_out):
    ### BEGIN SOLUTION
    tp = 40.0  # processing time
    while True:
        x = yield env.execute(c_in.receive())
        yield env.timeout(tp) 
        yield env.execute(c_out.send(x))
    ### END SOLUTION
        
# =================================
# Model
# =================================
def model():
    env = Environment()
    a = Channel(env)
    b = Channel(env)
    c = Channel(env)
    G = Generator(env, a)
    D = Demand_Buffer(env, a,b)
    V = Vehicle(env, b,c)
    E = Exit(env, c)
    env.run(until=E)
    print ("simulation has ended")

# =================================
# Main
# =================================
model()

tote =      1;  Entrytime =     0.0000;  Column =  3;  Mean throughput =0.025000  Mean flowtime = 40.0000
tote =      2;  Entrytime =   290.8883;  Column = 45;  Mean throughput =0.006400  Mean flowtime = 30.8102
tote =      3;  Entrytime =   290.8883;  Column = 45;  Mean throughput =0.008510  Mean flowtime = 41.0802
tote =      4;  Entrytime =   405.1957;  Column = 39;  Mean throughput =0.009446  Mean flowtime = 35.3713
tote =      5;  Entrytime =   405.1957;  Column = 39;  Mean throughput =0.010789  Mean flowtime = 39.9459
tote =      6;  Entrytime =   515.9801;  Column = 13;  Mean throughput =0.011570  Mean flowtime = 33.7236
tote =      7;  Entrytime =   521.2273;  Column = 52;  Mean throughput =0.012531  Mean flowtime = 34.2439
tote =      8;  Entrytime =   521.2273;  Column = 52;  Mean throughput =0.013365  Mean flowtime = 39.6341
tote =      9;  Entrytime =   674.4144;  Column = 39;  Mean throughput =0.013088  Mean flowtime = 36.7026
tote =     10;  Entrytime =   674.4144;  Colum

tote =    436;  Entrytime =  30720.1387;  Column = 38;  Mean throughput =0.014168  Mean flowtime = 39.3488
tote =    437;  Entrytime =  30970.3964;  Column = 44;  Mean throughput =0.014103  Mean flowtime = 39.2964
tote =    438;  Entrytime =  31014.5784;  Column = 24;  Mean throughput =0.014117  Mean flowtime = 39.2347
tote =    439;  Entrytime =  31056.3864;  Column = 37;  Mean throughput =0.014131  Mean flowtime = 39.1691
tote =    440;  Entrytime =  31056.3864;  Column = 37;  Mean throughput =0.014145  Mean flowtime = 39.1948
tote =    441;  Entrytime =  31150.7656;  Column = 45;  Mean throughput =0.014139  Mean flowtime = 39.1966
tote =    442;  Entrytime =  31227.1289;  Column =  4;  Mean throughput =0.014136  Mean flowtime = 39.1984
tote =    443;  Entrytime =  31400.4996;  Column =  3;  Mean throughput =0.014108  Mean flowtime = 39.1102
tote =    444;  Entrytime =  31400.4996;  Column =  3;  Mean throughput =0.014122  Mean flowtime = 39.1124
tote =    445;  Entrytime =  31452.24

tote =    935;  Entrytime =  66990.4372;  Column = 37;  Mean throughput =0.013954  Mean flowtime = 39.4789
tote =    936;  Entrytime =  67036.8761;  Column =  4;  Mean throughput =0.013960  Mean flowtime = 39.4469
tote =    937;  Entrytime =  67036.8761;  Column =  4;  Mean throughput =0.013967  Mean flowtime = 39.4576
tote =    938;  Entrytime =  67087.2548;  Column = 43;  Mean throughput =0.013974  Mean flowtime = 39.4572
tote =    939;  Entrytime =  67157.7274;  Column =  6;  Mean throughput =0.013980  Mean flowtime = 39.4244
tote =    940;  Entrytime =  67157.7274;  Column =  6;  Mean throughput =0.013987  Mean flowtime = 39.4342
tote =    941;  Entrytime =  67326.3932;  Column = 14;  Mean throughput =0.013977  Mean flowtime = 39.3932
tote =    942;  Entrytime =  67326.3932;  Column = 14;  Mean throughput =0.013983  Mean flowtime = 39.3947
tote =    943;  Entrytime =  67326.3932;  Column = 14;  Mean throughput =0.013990  Mean flowtime = 39.4386
tote =    944;  Entrytime =  67505.21

tote =   1435;  Entrytime =  101904.9897;  Column = 45;  Mean throughput =0.014081  Mean flowtime = 39.5830
tote =   1436;  Entrytime =  101904.9897;  Column = 45;  Mean throughput =0.014085  Mean flowtime = 39.5891
tote =   1437;  Entrytime =  101993.8788;  Column = 28;  Mean throughput =0.014087  Mean flowtime = 39.5703
tote =   1438;  Entrytime =  101993.8788;  Column = 28;  Mean throughput =0.014092  Mean flowtime = 39.5794
tote =   1439;  Entrytime =  102145.9570;  Column = 30;  Mean throughput =0.014082  Mean flowtime = 39.5797
tote =   1440;  Entrytime =  102215.5624;  Column = 11;  Mean throughput =0.014082  Mean flowtime = 39.5799
tote =   1441;  Entrytime =  102377.9629;  Column = 53;  Mean throughput =0.014070  Mean flowtime = 39.5802
tote =   1442;  Entrytime =  102426.0284;  Column =  2;  Mean throughput =0.014073  Mean flowtime = 39.5805
tote =   1443;  Entrytime =  102503.2347;  Column = 43;  Mean throughput =0.014077  Mean flowtime = 39.5570
tote =   1444;  Entrytime = 

tote =   1934;  Entrytime =  137657.8651;  Column = 26;  Mean throughput =0.014045  Mean flowtime = 39.4842
tote =   1935;  Entrytime =  137704.1129;  Column = 45;  Mean throughput =0.014048  Mean flowtime = 39.4845
tote =   1936;  Entrytime =  137872.5113;  Column =  5;  Mean throughput =0.014042  Mean flowtime = 39.4656
tote =   1937;  Entrytime =  137877.7544;  Column = 43;  Mean throughput =0.014045  Mean flowtime = 39.4648
tote =   1938;  Entrytime =  137936.7085;  Column = 31;  Mean throughput =0.014048  Mean flowtime = 39.4541
tote =   1939;  Entrytime =  137936.7085;  Column = 31;  Mean throughput =0.014051  Mean flowtime = 39.4641
tote =   1940;  Entrytime =  138018.4148;  Column =  4;  Mean throughput =0.014054  Mean flowtime = 39.4526
tote =   1941;  Entrytime =  138063.7927;  Column =  4;  Mean throughput =0.014058  Mean flowtime = 39.4384
tote =   1942;  Entrytime =  138063.7927;  Column =  4;  Mean throughput =0.014061  Mean flowtime = 39.4447
tote =   1943;  Entrytime = 

...

tote =   7928;  Entrytime =  549486.4528;  Column = 44;  Mean throughput =0.014428  Mean flowtime = 39.5812
tote =   7929;  Entrytime =  549486.4528;  Column = 44;  Mean throughput =0.014428  Mean flowtime = 39.5829
tote =   7930;  Entrytime =  549573.1799;  Column = 54;  Mean throughput =0.014429  Mean flowtime = 39.5790
tote =   7931;  Entrytime =  549621.4682;  Column = 44;  Mean throughput =0.014430  Mean flowtime = 39.5741
tote =   7932;  Entrytime =  549646.1863;  Column = 35;  Mean throughput =0.014431  Mean flowtime = 39.5711
tote =   7933;  Entrytime =  549646.1863;  Column = 35;  Mean throughput =0.014431  Mean flowtime = 39.5731
tote =   7934;  Entrytime =  549756.2381;  Column =  6;  Mean throughput =0.014431  Mean flowtime = 39.5731
tote =   7935;  Entrytime =  549942.3562;  Column =  7;  Mean throughput =0.014428  Mean flowtime = 39.5732
tote =   7936;  Entrytime =  550087.4450;  Column = 54;  Mean throughput =0.014426  Mean flowtime = 39.5704
tote =   7937;  Entrytime = 

tote =   8428;  Entrytime =  582908.8026;  Column = 48;  Mean throughput =0.014458  Mean flowtime = 39.5677
tote =   8429;  Entrytime =  582934.8206;  Column =  3;  Mean throughput =0.014459  Mean flowtime = 39.5659
tote =   8430;  Entrytime =  582934.8206;  Column =  3;  Mean throughput =0.014460  Mean flowtime = 39.5687
tote =   8431;  Entrytime =  583001.0076;  Column = 28;  Mean throughput =0.014460  Mean flowtime = 39.5688
tote =   8432;  Entrytime =  583160.8183;  Column = 10;  Mean throughput =0.014459  Mean flowtime = 39.5669
tote =   8433;  Entrytime =  583160.8183;  Column = 10;  Mean throughput =0.014459  Mean flowtime = 39.5697
tote =   8434;  Entrytime =  583229.6266;  Column = 38;  Mean throughput =0.014460  Mean flowtime = 39.5698
tote =   8435;  Entrytime =  583309.7534;  Column = 16;  Mean throughput =0.014460  Mean flowtime = 39.5698
tote =   8436;  Entrytime =  583618.5701;  Column = 18;  Mean throughput =0.014454  Mean flowtime = 39.5699
tote =   8437;  Entrytime = 

tote =   8927;  Entrytime =  617851.5404;  Column = 42;  Mean throughput =0.014448  Mean flowtime = 39.6358
tote =   8928;  Entrytime =  617851.5404;  Column = 42;  Mean throughput =0.014449  Mean flowtime = 39.6376
tote =   8929;  Entrytime =  617910.3648;  Column =  2;  Mean throughput =0.014449  Mean flowtime = 39.6376
tote =   8930;  Entrytime =  618091.3001;  Column = 31;  Mean throughput =0.014447  Mean flowtime = 39.6376
tote =   8931;  Entrytime =  618171.6323;  Column =  0;  Mean throughput =0.014447  Mean flowtime = 39.6363
tote =   8932;  Entrytime =  618218.1091;  Column = 47;  Mean throughput =0.014447  Mean flowtime = 39.6342
tote =   8933;  Entrytime =  618266.0880;  Column = 29;  Mean throughput =0.014448  Mean flowtime = 39.6313
tote =   8934;  Entrytime =  618297.4849;  Column = 31;  Mean throughput =0.014449  Mean flowtime = 39.6293
tote =   8935;  Entrytime =  618297.4849;  Column = 31;  Mean throughput =0.014450  Mean flowtime = 39.6318
tote =   8936;  Entrytime = 

tote =   9427;  Entrytime =  651710.3539;  Column = 40;  Mean throughput =0.014464  Mean flowtime = 39.6198
tote =   9428;  Entrytime =  651761.8438;  Column = 49;  Mean throughput =0.014465  Mean flowtime = 39.6198
tote =   9429;  Entrytime =  651849.4082;  Column = 35;  Mean throughput =0.014464  Mean flowtime = 39.6198
tote =   9430;  Entrytime =  651951.2527;  Column = 40;  Mean throughput =0.014463  Mean flowtime = 39.6199
tote =   9431;  Entrytime =  652058.3789;  Column =  0;  Mean throughput =0.014463  Mean flowtime = 39.6162
tote =   9432;  Entrytime =  652058.3789;  Column =  0;  Mean throughput =0.014464  Mean flowtime = 39.6167
tote =   9433;  Entrytime =  652122.5049;  Column = 50;  Mean throughput =0.014464  Mean flowtime = 39.6167
tote =   9434;  Entrytime =  652251.3611;  Column = 28;  Mean throughput =0.014463  Mean flowtime = 39.6139
tote =   9435;  Entrytime =  652298.1798;  Column = 36;  Mean throughput =0.014464  Mean flowtime = 39.6103
tote =   9436;  Entrytime = 

tote =   9926;  Entrytime =  686127.9739;  Column = 44;  Mean throughput =0.014466  Mean flowtime = 39.6139
tote =   9927;  Entrytime =  686148.6659;  Column = 43;  Mean throughput =0.014467  Mean flowtime = 39.6128
tote =   9928;  Entrytime =  686148.6659;  Column = 43;  Mean throughput =0.014468  Mean flowtime = 39.6158
tote =   9929;  Entrytime =  686277.3712;  Column = 10;  Mean throughput =0.014467  Mean flowtime = 39.6158
tote =   9930;  Entrytime =  686437.7096;  Column =  2;  Mean throughput =0.014465  Mean flowtime = 39.6159
tote =   9931;  Entrytime =  686486.1290;  Column = 36;  Mean throughput =0.014466  Mean flowtime = 39.6159
tote =   9932;  Entrytime =  686644.2806;  Column = 19;  Mean throughput =0.014464  Mean flowtime = 39.6159
tote =   9933;  Entrytime =  686762.9201;  Column = 36;  Mean throughput =0.014463  Mean flowtime = 39.6137
tote =   9934;  Entrytime =  686762.9201;  Column = 36;  Mean throughput =0.014464  Mean flowtime = 39.6155
tote =   9935;  Entrytime = 

c. Confirm that your simulations produce the correct throughput and flow time.

Answer: ...



d. Run your simulation at least 10 times. What is the range of outcomes for the mean throughput? Determine (roughly/ by trial and error) the number of orders required to get good estimates for the flow time (first three non-zero digits are correct).

Answer: ...



## 6.4 Exercise 4: Vehicle accurately modelled (15 points)
Assume that a vehicle starts from the buffer. If it has to go to column $i \in \{0, depth - 1\}$, it needs to drive a distance $dv \cdot (i + 1)$, pick up the tote, drive back, and deliver the tote to the buffer. For driving the required distance, the vehicle first goes with a constant acceleration `av` *m/s$^2$* until it reaches its maximum velocity `vmaxv`, then it moves with this velocity and decelerates with a constant deceleration `av` to approach its destination point. If the tote is located too close to the end of the aisle, it is possible that the vehicle will not reach its maximum speed. 

a. From this information, (analytically) determine the time (in seconds) it takes a vehicle to drive a given distance of x meters. To that end, first determine from the acceleration profile the travelled distance as function of time. From that you can determine the time required to travel a given distance.

Answer: ...



b. Next, if loading and unloading a tote both take `lv` seconds, determine (analytically) the time it takes a vehicle, starting from the buffer, to pick up a tote from column $i \in \{0, depth\}$ and deliver it to the buffer.

Answer: ...



c. Determine (analytically) the mean and variance of this total travel time for a random (uniformly distributed) column.

Answer: ...



d. Determine (analytically) the throughput and flow time that should result from your model with only the generator process, demand buffer, vehicle and the exit process.

Answer: ...



e. Complete the simulation code in the template below, incorporating the actual time a vehicle requires for picking up a tote and delivering it to the buffer.

Note: the previously defined function processes remain unchanged, only the Vehicle needs to be redefined.

In [6]:
# =================================
# Global vehicle variables
# =================================
lv = 3.0                  # time to load/unload the vehicle
dv = 0.5                  # unit width clearance
vmaxv = 1.5              # maximum velocity of the vehicle
av = 1.0                  # acceleration/deceleration of the vehicle

# =================================
# Vehicle definition
# =================================
@process
def Vehicle(env, c_in, c_out):
    ### BEGIN SOLUTION
    while True: 
        x = yield env.execute(c_in.receive())
        distance = dv*(x.column+1)
        if distance <= vmaxv**2/av:
            duration = 4*math.sqrt(distance/av) + 2*lv
        else:
            duration = 2*(distance/vmaxv + vmaxv/av + lv)
        yield env.timeout(duration)
        yield env.execute(c_out.send(x) )
    ### END SOLUTION

# =================================
# Main
# =================================
def model():
    env = Environment()
    a = Channel(env)
    b = Channel(env)
    c = Channel(env)
    G = Generator(env, a)
    D = Demand_Buffer(env, a,b)
    V = Vehicle(env, b,c)
    E = Exit(env, c)
    env.run(until=E)
    print ("simulation has ended")

# =================================
# Main
# =================================
model()


tote =      1;  Entrytime =     0.0000;  Column = 49;  Mean throughput =0.023622  Mean flowtime = 42.3333
tote =      2;  Entrytime =   129.1939;  Column = 48;  Mean throughput =0.013294  Mean flowtime = 31.7926
tote =      3;  Entrytime =   190.9177;  Column = 52;  Mean throughput =0.015616  Mean flowtime = 21.5933
tote =      4;  Entrytime =   190.9177;  Column = 52;  Mean throughput =0.016917  Mean flowtime = 27.5770
tote =      5;  Entrytime =   275.8074;  Column =  4;  Mean throughput =0.017808  Mean flowtime = 23.0560
tote =      6;  Entrytime =   290.9136;  Column = 10;  Mean throughput =0.020470  Mean flowtime = 19.5798
tote =      7;  Entrytime =   290.9136;  Column = 10;  Mean throughput =0.022621  Mean flowtime = 19.4301
tote =      8;  Entrytime =   311.4816;  Column =  4;  Mean throughput =0.024705  Mean flowtime = 18.5430
tote =      9;  Entrytime =   370.6819;  Column = 32;  Mean throughput =0.022406  Mean flowtime = 19.9271
tote =     10;  Entrytime =   417.4805;  Colum

tote =    419;  Entrytime =  29218.2251;  Column = 37;  Mean throughput =0.014318  Mean flowtime = 29.5354
tote =    420;  Entrytime =  29218.2251;  Column = 37;  Mean throughput =0.014335  Mean flowtime = 29.6549
tote =    421;  Entrytime =  29420.5656;  Column = 14;  Mean throughput =0.014301  Mean flowtime = 29.6264
tote =    422;  Entrytime =  29455.6924;  Column =  2;  Mean throughput =0.014326  Mean flowtime = 29.5598
tote =    423;  Entrytime =  29455.6924;  Column =  2;  Mean throughput =0.014354  Mean flowtime = 29.5193
tote =    424;  Entrytime =  29455.6924;  Column =  2;  Mean throughput =0.014383  Mean flowtime = 29.5047
tote =    425;  Entrytime =  29455.6924;  Column =  2;  Mean throughput =0.014412  Mean flowtime = 29.5157
tote =    426;  Entrytime =  29455.6924;  Column =  2;  Mean throughput =0.014440  Mean flowtime = 29.5524
tote =    427;  Entrytime =  29569.4478;  Column =  2;  Mean throughput =0.014437  Mean flowtime = 29.5023
tote =    428;  Entrytime =  29569.44

tote =    918;  Entrytime =  61156.1745;  Column = 12;  Mean throughput =0.015006  Mean flowtime = 28.5076
tote =    919;  Entrytime =  61194.0165;  Column = 33;  Mean throughput =0.015010  Mean flowtime = 28.5110
tote =    920;  Entrytime =  61315.4187;  Column = 17;  Mean throughput =0.014999  Mean flowtime = 28.5028
tote =    921;  Entrytime =  61516.1205;  Column = 26;  Mean throughput =0.014969  Mean flowtime = 28.4853
tote =    922;  Entrytime =  61516.1205;  Column = 26;  Mean throughput =0.014978  Mean flowtime = 28.4970
tote =    923;  Entrytime =  61573.2881;  Column = 45;  Mean throughput =0.014981  Mean flowtime = 28.5091
tote =    924;  Entrytime =  61622.8799;  Column = 13;  Mean throughput =0.014990  Mean flowtime = 28.4981
tote =    925;  Entrytime =  61808.3658;  Column =  2;  Mean throughput =0.014965  Mean flowtime = 28.4695
tote =    926;  Entrytime =  61808.3658;  Column =  2;  Mean throughput =0.014979  Mean flowtime = 28.4527
tote =    927;  Entrytime =  61889.69

tote =   1418;  Entrytime =  94984.4612;  Column = 18;  Mean throughput =0.014927  Mean flowtime = 27.8706
tote =   1419;  Entrytime =  94984.4612;  Column = 18;  Mean throughput =0.014934  Mean flowtime = 27.8725
tote =   1420;  Entrytime =  95192.2379;  Column = 21;  Mean throughput =0.014913  Mean flowtime = 27.8695
tote =   1421;  Entrytime =  95218.2720;  Column =  5;  Mean throughput =0.014922  Mean flowtime = 27.8591
tote =   1422;  Entrytime =  95306.6966;  Column = 26;  Mean throughput =0.014916  Mean flowtime = 27.8585
tote =   1423;  Entrytime =  95472.8550;  Column = 28;  Mean throughput =0.014903  Mean flowtime = 27.8458
tote =   1424;  Entrytime =  95472.8550;  Column = 28;  Mean throughput =0.014909  Mean flowtime = 27.8529
tote =   1425;  Entrytime =  95472.8550;  Column = 28;  Mean throughput =0.014915  Mean flowtime = 27.8800
tote =   1426;  Entrytime =  95572.7324;  Column = 46;  Mean throughput =0.014914  Mean flowtime = 27.8887
tote =   1427;  Entrytime =  95628.39

tote =   1917;  Entrytime =  128984.4935;  Column = 38;  Mean throughput =0.014862  Mean flowtime = 27.4611
tote =   1918;  Entrytime =  129010.4850;  Column = 28;  Mean throughput =0.014865  Mean flowtime = 27.4538
tote =   1919;  Entrytime =  129026.8015;  Column = 51;  Mean throughput =0.014870  Mean flowtime = 27.4527
tote =   1920;  Entrytime =  129054.8296;  Column =  6;  Mean throughput =0.014873  Mean flowtime = 27.4597
tote =   1921;  Entrytime =  129054.8296;  Column =  6;  Mean throughput =0.014879  Mean flowtime = 27.4739
tote =   1922;  Entrytime =  129231.3389;  Column = 41;  Mean throughput =0.014868  Mean flowtime = 27.4788
tote =   1923;  Entrytime =  129399.1771;  Column = 42;  Mean throughput =0.014857  Mean flowtime = 27.4841
tote =   1924;  Entrytime =  129517.0109;  Column = 36;  Mean throughput =0.014851  Mean flowtime = 27.4873
tote =   1925;  Entrytime =  129641.9643;  Column =  6;  Mean throughput =0.014847  Mean flowtime = 27.4802
tote =   1926;  Entrytime = 

...

tote =   7911;  Entrytime =  541806.8335;  Column = 33;  Mean throughput =0.014600  Mean flowtime = 27.3957
tote =   7912;  Entrytime =  542036.6531;  Column = 22;  Mean throughput =0.014596  Mean flowtime = 27.3953
tote =   7913;  Entrytime =  542172.1014;  Column =  4;  Mean throughput =0.014595  Mean flowtime = 27.3934
tote =   7914;  Entrytime =  542280.1867;  Column =  9;  Mean throughput =0.014594  Mean flowtime = 27.3919
tote =   7915;  Entrytime =  542402.5765;  Column =  7;  Mean throughput =0.014592  Mean flowtime = 27.3902
tote =   7916;  Entrytime =  542476.0704;  Column =  5;  Mean throughput =0.014592  Mean flowtime = 27.3884
tote =   7917;  Entrytime =  542507.6964;  Column = 38;  Mean throughput =0.014592  Mean flowtime = 27.3894
tote =   7918;  Entrytime =  542553.9180;  Column = 37;  Mean throughput =0.014593  Mean flowtime = 27.3903
tote =   7919;  Entrytime =  542638.6487;  Column =  9;  Mean throughput =0.014593  Mean flowtime = 27.3888
tote =   7920;  Entrytime = 

tote =   8411;  Entrytime =  582386.1096;  Column =  2;  Mean throughput =0.014442  Mean flowtime = 27.3770
tote =   8412;  Entrytime =  582479.1965;  Column = 41;  Mean throughput =0.014441  Mean flowtime = 27.3782
tote =   8413;  Entrytime =  582642.5334;  Column =  1;  Mean throughput =0.014439  Mean flowtime = 27.3761
tote =   8414;  Entrytime =  582790.4289;  Column = 23;  Mean throughput =0.014437  Mean flowtime = 27.3755
tote =   8415;  Entrytime =  582790.4289;  Column = 23;  Mean throughput =0.014438  Mean flowtime = 27.3780
tote =   8416;  Entrytime =  583027.7042;  Column =  7;  Mean throughput =0.014435  Mean flowtime = 27.3764
tote =   8417;  Entrytime =  583104.8278;  Column = 39;  Mean throughput =0.014434  Mean flowtime = 27.3774
tote =   8418;  Entrytime =  583145.9250;  Column = 54;  Mean throughput =0.014435  Mean flowtime = 27.3779
tote =   8419;  Entrytime =  583215.5467;  Column = 22;  Mean throughput =0.014435  Mean flowtime = 27.3756
tote =   8420;  Entrytime = 

tote =   8910;  Entrytime =  618635.2051;  Column = 16;  Mean throughput =0.014402  Mean flowtime = 27.4332
tote =   8911;  Entrytime =  618827.6181;  Column = 28;  Mean throughput =0.014400  Mean flowtime = 27.4302
tote =   8912;  Entrytime =  618836.6498;  Column = 16;  Mean throughput =0.014401  Mean flowtime = 27.4294
tote =   8913;  Entrytime =  618860.5379;  Column = 48;  Mean throughput =0.014402  Mean flowtime = 27.4283
tote =   8914;  Entrytime =  618895.8930;  Column = 11;  Mean throughput =0.014403  Mean flowtime = 27.4278
tote =   8915;  Entrytime =  618895.8930;  Column = 11;  Mean throughput =0.014404  Mean flowtime = 27.4292
tote =   8916;  Entrytime =  618895.8930;  Column = 11;  Mean throughput =0.014405  Mean flowtime = 27.4326
tote =   8917;  Entrytime =  618954.9213;  Column =  3;  Mean throughput =0.014406  Mean flowtime = 27.4308
tote =   8918;  Entrytime =  619058.7880;  Column = 19;  Mean throughput =0.014405  Mean flowtime = 27.4302
tote =   8919;  Entrytime = 

tote =   9410;  Entrytime =  653797.0810;  Column = 32;  Mean throughput =0.014392  Mean flowtime = 27.4610
tote =   9411;  Entrytime =  653833.2141;  Column = 33;  Mean throughput =0.014393  Mean flowtime = 27.4614
tote =   9412;  Entrytime =  653902.2123;  Column = 32;  Mean throughput =0.014393  Mean flowtime = 27.4618
tote =   9413;  Entrytime =  653957.3514;  Column = 36;  Mean throughput =0.014393  Mean flowtime = 27.4624
tote =   9414;  Entrytime =  654141.1690;  Column = 21;  Mean throughput =0.014391  Mean flowtime = 27.4628
tote =   9415;  Entrytime =  654178.0123;  Column = 15;  Mean throughput =0.014392  Mean flowtime = 27.4617
tote =   9416;  Entrytime =  654214.8149;  Column = 27;  Mean throughput =0.014393  Mean flowtime = 27.4588
tote =   9417;  Entrytime =  654214.8149;  Column = 27;  Mean throughput =0.014394  Mean flowtime = 27.4588
tote =   9418;  Entrytime =  654325.2998;  Column = 15;  Mean throughput =0.014393  Mean flowtime = 27.4589
tote =   9419;  Entrytime = 

tote =   9909;  Entrytime =  686874.2884;  Column = 44;  Mean throughput =0.014425  Mean flowtime = 27.4630
tote =   9910;  Entrytime =  686935.9863;  Column = 53;  Mean throughput =0.014426  Mean flowtime = 27.4619
tote =   9911;  Entrytime =  686935.9863;  Column = 53;  Mean throughput =0.014427  Mean flowtime = 27.4654
tote =   9912;  Entrytime =  687014.9551;  Column = 11;  Mean throughput =0.014427  Mean flowtime = 27.4643
tote =   9913;  Entrytime =  687066.7217;  Column = 11;  Mean throughput =0.014428  Mean flowtime = 27.4633
tote =   9914;  Entrytime =  687179.1454;  Column = 39;  Mean throughput =0.014426  Mean flowtime = 27.4641
tote =   9915;  Entrytime =  687297.2268;  Column = 40;  Mean throughput =0.014425  Mean flowtime = 27.4650
tote =   9916;  Entrytime =  687378.9809;  Column = 36;  Mean throughput =0.014426  Mean flowtime = 27.4636
tote =   9917;  Entrytime =  687378.9809;  Column = 36;  Mean throughput =0.014426  Mean flowtime = 27.4655
tote =   9918;  Entrytime = 

f. Confirm that your simulations produce the correct throughput and flow time.

Answer: ...



g.  Run your simulation at least 10 times. What is the range of outcomes for the mean throughput? Determine (roughly, by trial and error) the number of orders required to get good estimates for the flow time (first three non-zero digits are correct).

Answer: ...



## 6.5 Exercise 5: Lift as two stage machine (5 points)
In the previous exercises we focussed on modeling a tier. In exercises 5-8 we focus on modeling the Buffer and Lift, starting with the Lift. We model the Lift as a machine, which repeatedly does the following: request a destination tier, move to the desired tier, receive a tote (first delay for `ll`, then communicate), move to the ground floor, deliver the tote (first delay for `ll`, then communicate). In this exercise we assume that moving to the desired tier takes 23.0 seconds, receiving the tote takes 2.0 seconds, moving to the ground floor again takes 23.0 seconds, and delivering the tote also takes 2.0 seconds. Note that, in this case, this implies that the tote should leave the Generator and enter the Lift 25.0 seconds after the Lift has received the destination tier. All of these times are assumed to be deterministic.

a. Assume that after 1.0 second the first tote arrives. Subsequently a tote arrives respectively 10.0, 100.0, and 100.0 seconds after the completion of sending its predecessor to the buffer. Make a lot-time-diagram indicating how long a newly generated job spends in the Generator, and spends in the Lift.

Answer: attach figure

b. Complete the simulation code in the template below, incorporating the actual time a vehicle requires for picking up a tote and delivering it to the buffer.

In [7]:
# =================================
# Tote definition
# =================================
@dataclass
class Tote:
    entrytime: float = 0
    tier: int = 0

# =================================
# Global Lift variables
# =================================
ll = 2.0  # time to load/unload the lift


# =================================
# Generator
# =================================
@process
def Generator(env, c_out, c_lift):
    delays=[1.0, 10.0, 100.0, 100.0]
    while len(delays)>0:
        yield env.timeout(delays[0])
        delays = delays[1:]
        yield env.execute(c_lift.send(1))
        print(f"Generator: Informed Lift to go to tier 1 at time {env.now:3.1f}");
        x = Tote(entrytime = env.now, tier = 1)
        yield env.execute(c_out.send(x))
        print(f"Generator: Tote has completely left the Generator and entered the Lift at time {env.now:3.1f}")
    yield env.timeout(100.0)


# =================================
# Lift
# =================================
@process
def Lift(env, c_in, c_lift, c_out):
    ### BEGIN SOLUTION
    while True:
        lift_called = c_lift.receive()
        destination = yield env.execute(lift_called)
        yield env.timeout(23.0+ll)
        x = yield env.execute(c_in.receive())
        yield env.timeout(23.0+ll)
        yield env.execute(c_out.send(x))
    ### END SOLUTION

    
# =================================
# Exit 
# =================================
@process
def Exit(env, c_in):
    while True:
        x = yield env.execute(c_in.receive())
        print(f"Exit:      Tote has completely left the Lift and has been received by the Exit at time {env.now:3.1f}");

# =================================
# Model
# =================================
def model():
    env = Environment()
    a = Channel(env)  # for sending lots
    b = Channel(env)  # lift tier
    c = Channel(env)  # for sending lots
    G = Generator(env, a, b)
    L = Lift(env, a, b, c)
    E = Exit(env, c)
    env.run()
    print ("simulation has ended")

# =================================
# Main
# =================================
model()

Generator: Informed Lift to go to tier 1 at time 1.0
Generator: Tote has completely left the Generator and entered the Lift at time 26.0
Exit:      Tote has completely left the Lift and has been received by the Exit at time 51.0
Generator: Informed Lift to go to tier 1 at time 51.0
Generator: Tote has completely left the Generator and entered the Lift at time 76.0
Exit:      Tote has completely left the Lift and has been received by the Exit at time 101.0
Generator: Informed Lift to go to tier 1 at time 176.0
Generator: Tote has completely left the Generator and entered the Lift at time 201.0
Exit:      Tote has completely left the Lift and has been received by the Exit at time 226.0
Generator: Informed Lift to go to tier 1 at time 301.0
Generator: Tote has completely left the Generator and entered the Lift at time 326.0
Exit:      Tote has completely left the Lift and has been received by the Exit at time 351.0
simulation has ended


c. Confirm that your simulations produce the correct results, i.e., in correspondence with your lot-time-diagram.

Answer: ...



## 6.6 Exercise 6: Buffer with only one tier (5 points)
In case we have only one tier, we could use a standard model for a finite buffer. However, keeping in mind that we need to model in the next exercise Level finite buffers in parallel where totes are served at a first-come-first-serve basis, we model the finite buffer slightly differently. We have a counter `n` which counts the number of jobs in the buffer, and we keep a list `xs` of totes that have arrived to the buffer. As long as the buffer contains less than `bc` totes, the buffer can receive jobs. Furthermore, if the buffer contains totes, it is possible to receive a request from the Lift (asking for which tier to move to, which is always 0 in this case). Additionally, if the buffer contains totes it is possible to send the first tote of the list `xs` to the lift.

a. Assume that after 1.0 second the first tote arrives. Subsequently, a tote arrives respectively 10.0, 100.0, and 100.0 seconds after the completion of sending its predecessor to the buffer. Make a lot-time-diagram indicating how long a newly generated job spends in the Generator, in the Buffer, and spends in the Lift.

Answer: attach figure

 b. Complete the simulation code in the template below, only the Generator and Buffer need to be redefined.

In [8]:
# =================================
# Global Lift variables
# =================================
ll = 2.0  # time to load/unload the lift
bc = 1    # buffer capacity

# =================================
# Generator
# =================================
@process
def Generator(env, c_out):
    delays=[1.0, 10.0, 100.0, 100.0]
    while len(delays)>0:
        yield env.timeout(delays[0])
        delays = delays[1:]
        x = Tote(entrytime = env.now, tier = 0)
        yield env.execute(c_out.send(x))
        print(f"Generator: sending tote to Buffer at time {env.now:3.1f}")
    yield env.timeout(100.0)

# =================================
# Buffer
# =================================
@process
def Buffer(env, c_in, c_out, c_lift):
    xs = [] # list of jobs
    n = 0
    while True:
        receiving = c_in.receive() if n < bc else None
        call_lift = c_lift.send(xs[0].tier) if len(xs) > 0 else None
        sending   = c_out.send(xs[0]) if len(xs)>0 else None
        
        yield env.select(receiving, call_lift, sending)

        if selected(receiving):
            x = receiving.entity
            xs = xs + [x]
            n = n+1
        
        if selected(call_lift):
            pass
        
        if selected(sending):
            ### BEGIN SOLUTION
            xs = xs[1:]
            n = n - 1
            ### END SOLUTION
            
# =================================
# Model
# =================================
def model():
    env = Environment()
    a = Channel(env)  # for sending lots
    b = Channel(env)  # for sending lots
    c = Channel(env)  # for calling the lift
    d = Channel(env)  # for sending lots

    G = Generator(env, a)
    B = Buffer(env, a, b, c)
    L = Lift(env, b, c, d)
    E = Exit(env, d)
    env.run()
    print ("simulation has ended")

# =================================
# Main
# =================================
model()

Generator: sending tote to Buffer at time 1.0
Generator: sending tote to Buffer at time 26.0
Exit:      Tote has completely left the Lift and has been received by the Exit at time 51.0
Exit:      Tote has completely left the Lift and has been received by the Exit at time 101.0
Generator: sending tote to Buffer at time 126.0
Exit:      Tote has completely left the Lift and has been received by the Exit at time 176.0
Generator: sending tote to Buffer at time 226.0
Exit:      Tote has completely left the Lift and has been received by the Exit at time 276.0
simulation has ended


c. Confirm that your simulations produce the correct results, i.e., in correspondence with your lot-time-diagram

Answer: ...



## Exercise 7: Buffer with multiple tiers (5 points)
We extend the buffer from the previous exercise to `Level` parallel finite buffers of size `bc` which are modelled as a list of `Level` counters. For this list we use the variable `n`. We keep a common list `xs` of totes that have arrived to all buffers. This list is used to determine which tote should be picked up first by the Lift. For each of the tiers it holds that if the buffer of that tier is not full yet, a tote can be received. Furthermore, if the buffer contains totes, it is possible to receive a request from the Lift asking for the tier to move to. Additionally, if the buffer contains totes it is possible to send the first tote of the list `xs` to the lift.

a. Consider two tiers, and assume that after `Tier` seconds the first tote arrives (for two tiers: after 0.0 for tier 0 and
after 1.0 for tier 1). Subsequently a tote arrives respectively 10.0, 100.0, and 100.0 seconds after the completion
of sending its predecessor to the buffer. Make a lot-time-diagram indicating how long a newly generated job
spends in which Generator, in the Buffer, and spends in the Lift.

Answer: attach figure

b. Complete the simulation code in the template below.

In [9]:
# =================================
# Global variables
# =================================
ll = 2.0  # time to load/unload the lift
bc = 1    # buffer capacity
Level = 2 # the number of tiers

# =================================
# Generator
# =================================
@process
def Generator(env, c_out, level):
    delays=[1.0*level, 10.0, 100.0, 100.0]
    while len(delays)>0:
        yield env.timeout(delays[0])
        delays = delays[1:]
        x = Tote(entrytime = env.now, tier = level)
        yield env.execute(c_out.send(x))
        print(f"Generator {level:d}: Sending tote to Buffer completed at "
              f"time {env.now:3.1f}")
    yield env.timeout(100.0)
    
# =================================
# Buffer
# =================================
@process
def Buffer(env, c_in, c_out, c_lift):
    xs = []
    n = [0] * Level
    while True:
        receiving = [c_in[Tier].receive() if n[Tier] < bc else None for Tier in range(Level) ]
        call_lift = c_lift.send(xs[0].tier) if len(xs) > 0 else None
        sending = c_out.send(xs[0]) if len(xs) > 0 else None
        communications = receiving + [call_lift] + [sending]

        yield env.select(*communications)
        
        for Tier in range(Level):
            if selected(receiving[Tier]):
                x = receiving[Tier].entity
                xs = xs + [x]
                n[Tier] = n[Tier] + 1
        
        if selected(call_lift):
            pass
            
        if selected(sending):
            ### BEGIN SOLUTION
            Tier = xs[0].tier 
            xs = xs[1:]
            n[Tier] = n[Tier] - 1
            ### END SOLUTION
            
# =================================
# Model
# =================================
def model():
    env = Environment()
    a = [Channel(env) for tier in range(Level)] # a channel for each tier, each sending lots
    b = Channel(env)  # for sending lots
    c = Channel(env)  # for calling the lift
    d = Channel(env)  # for sending lots
    Gs = [Generator(env, a[tier], tier) for tier in range(Level)] 
    B = Buffer(env, a, b, c)
    L = Lift(env, b, c, d)
    E = Exit(env, d)
    env.run(until=1000000)
    print ("simulation has ended")

# =================================
# Main
# =================================
model()

Generator 0: Sending tote to Buffer completed at time 0.0
Generator 1: Sending tote to Buffer completed at time 1.0
Generator 0: Sending tote to Buffer completed at time 25.0
Exit:      Tote has completely left the Lift and has been received by the Exit at time 50.0
Generator 1: Sending tote to Buffer completed at time 75.0
Exit:      Tote has completely left the Lift and has been received by the Exit at time 100.0
Generator 0: Sending tote to Buffer completed at time 125.0
Exit:      Tote has completely left the Lift and has been received by the Exit at time 150.0
Generator 1: Sending tote to Buffer completed at time 175.0
Exit:      Tote has completely left the Lift and has been received by the Exit at time 200.0
Generator 0: Sending tote to Buffer completed at time 225.0
Exit:      Tote has completely left the Lift and has been received by the Exit at time 250.0
Generator 1: Sending tote to Buffer completed at time 275.0
Exit:      Tote has completely left the Lift and has been rece

c. Confirm that your simulations produce the correct results, i.e., in correspondence with your lot-time-diagram

Answer: ...



## Exercise 8: Lift accurately modelled (5 points)

Assume that the Lift starts from the ground floor. If it has to go to level $i \in \{0, Level - 1\}$, it needs to travel a
distance $dl \cdot (i + 1)$, pick up the tote, travel back, and deliver the tote at the ground floor. For traveling the required
distance, the vehicle first goes with a constant acceleration `al` *m/s$^2$* until it reaches its maximum velocity `vmaxl`, then
it moves with this velocity and decelerates with a constant deceleration `al` to approach its destination tier. If the tier
is located too close to the ground floor, it is possible that the Lift will not reach its maximum speed.

a. From this information, (analytically) determine the time (in seconds) it takes the Lift to a given tier.

Answer: ...



b. Next, if loading and unloading a tote both take `ll` seconds, determine (analytically) the time it takes the Lift to pick up a tote from tier $i \in \{0, depth - 1\}$ and deliver it to the buffer.

Answer: ...



c. Consider two tiers, and assume that after Tier seconds the first tote arrives (for two tiers: after 0.0 for tier 0 and after 1.0 for tier 1). Subsequently a tote arrives respectively 10.0, 100.0, and 100.0 seconds after the completion of sending its predecessor to the buffer. Make a lot-time-diagram indicating how long a newly generated job spends in which Generator, in the Buffer, and spends in the Lift.

Answer: attach figure

d. Complete the simulation code in the template below.

In [10]:
# =================================
# Global variables
# =================================
ll = 2.0        # time to load/unload the lift
bc = 1          # buffer capacity
Level = 2       # the number of tiers
dl = 0.8        # unit height clearance
vmaxl = 5.0     # maximum velocity of lift
al = 7.0        # acceleration/deceleration of lift

# =================================
# Lift definition
# =================================
@process
def Lift(env, c_in, c_lift, c_out):
    while True: 
        ### BEGIN SOLUTION
        destination = yield env.execute(c_lift.receive())
        
        distance = dl * (destination+1)
        if distance <= vmaxl**2/al:
            duration = 2*math.sqrt(distance/al) + ll
        else:
            duration = distance/vmaxl +vmaxl/al + ll

        yield env.timeout(duration)
        x = yield env.execute(c_in.receive())
        yield env.timeout(duration)
        yield env.execute(c_out.send(x))
        ### END SOLUTION
        
        
# =================================
# Model
# =================================
def model():
    env = Environment()
    a = [Channel(env) for Tier in range(Level)] # a channel for each tier, each sending totes
    b = Channel(env)  # for sending totes
    c = Channel(env)  # for calling the lift
    d = Channel(env)  # for sending totes

    Gs = [Generator(env, a[Tier], Tier) for Tier in range(Level)] 
    B = Buffer(env, a, b, c)
    L = Lift(env, b, c, d)
    E = Exit(env, d)
    env.run()
    print ("simulation has ended")

    
# =================================
# Main
# =================================
model()

Generator 0: Sending tote to Buffer completed at time 0.0
Generator 1: Sending tote to Buffer completed at time 1.0
Exit:      Tote has completely left the Lift and has been received by the Exit at time 5.4
Generator 0: Sending tote to Buffer completed at time 10.0
Generator 1: Sending tote to Buffer completed at time 11.0
Exit:      Tote has completely left the Lift and has been received by the Exit at time 11.3
Exit:      Tote has completely left the Lift and has been received by the Exit at time 16.6
Exit:      Tote has completely left the Lift and has been received by the Exit at time 22.5
Generator 0: Sending tote to Buffer completed at time 110.0
Generator 1: Sending tote to Buffer completed at time 111.0
Exit:      Tote has completely left the Lift and has been received by the Exit at time 115.4
Exit:      Tote has completely left the Lift and has been received by the Exit at time 121.3
Generator 0: Sending tote to Buffer completed at time 210.0
Generator 1: Sending tote to Buff

e. Confirm that your simulations produce the correct results, i.e., in correspondence with your lot-time-diagram

Answer: ...



## 6.9 Exercise 9: Entire system (10 points)
In the previous exercises we developed and tested each process individually. Now it is time to combine all processes into one model.

a. Determine the (total) arrival rate of orders for a system with `Level` tiers, where for each tier orders arrive with a mean inter arrival time of `arrive`.

Answer: ...



b. Complete the simulation code in the template below by substituting the code for the processes as you derived in Exercises 1, 2, 4, 7, and 8. Note that the type tote has been extended in comparison with Exercise 1, so one line of code extra is required in the Generator process to include the tier.

In [14]:
# =================================
# Tote
# =================================
@dataclass
class Tote:
    entrytime: float = 0.0
    column: int = 0
    tier: int  = 0
        
# =================================
# Global variables
# =================================
lv = 3.0                   # time to load/unload the vehicle
dv = 0.5                   # unit width clearance
vmaxv = 1.5                # maximum velocity of the vehicle
av = 1.0                   # acceleration/deceleration of the vehicle
ll = 2.0                   # time to load/unload the lift
dl = 0.8                   # unit height clearance
vmaxl = 5.0                # maximum velocity of lift
al = 7.0                   # acceleration/deceleration of lift
bc = 1                     # buffer capacity
arrive = 70.0              # inter arrival time of requests
Level = 9                  # the number of tiers
depth  = 55                # the number of columns
number_of_orders = 100000  # the number of orders to process

# =================================
# Generator
# =================================
@process
def Generator(env, c_out, Tier):
    ### BEGIN SOLUTION
    ta_dist = lambda: random.exponential(arrive)
    column_dist = lambda:  random.randint(1, depth)
    ### END SOLUTION
    while True:
        x = Tote()
        x.entrytime = env.now
        # x.column = ..... 
        # x.tier = ..... 
        ### BEGIN SOLUTION
        x.column = column_dist()
        x.tier = Tier
        ### END SOLUTION
        yield env.execute(c_out.send(x))
        # delay = ..... 
        ### BEGIN SOLUTION
        delay = ta_dist()
        ### END SOLUTION
        yield env.timeout(delay)
        
        
# =================================
# Demand Buffer
# =================================
@process
def Demand_Buffer(env, c_in, c_out):
    xs = [] # list of totes
    while True:
        ### BEGIN SOLUTION
        receiving = c_in.receive() 
        sending = c_out.send(xs[0]) if len(xs)>0 else None
        yield env.select(sending,receiving)
        if selected(sending):
            xs = xs[1:]
        if selected(receiving):
            x = receiving.entity
            xs = xs + [x]
        ### END SOLUTION
            
            
# =================================
# Vehicle
# =================================
@process
def Vehicle(env, c_in, c_out):
    ### BEGIN SOLUTION
    while True:
        x = yield env.execute(c_in.receive())
        distance = dv*(x.column+1)
        if distance <= vmaxv**2/av:
            duration = 4*math.sqrt(distance/av) + 2*lv
        else:
            duration = 2*(distance/vmaxv + vmaxv/av + lv)
        yield env.timeout(duration)
        yield env.execute(c_out.send(x) )
    ### END SOLUTION


# =================================
# Buffer
# =================================
@process
def Buffer(env, c_in, c_out, c_lift):
    xs = []
    n = [0] * Level
    while True:
        receiving = [c_in[Tier].receive() if n[Tier] < bc else None for Tier in range(Level) ]
        call_lift = c_lift.send(xs[0].tier) if len(xs) > 0 else None
        sending = c_out.send(xs[0]) if len(xs) > 0 else None
        communications = receiving + [call_lift] + [sending]

        yield env.select(*communications)

        for Tier in range(Level):
            if selected(receiving[Tier]):
                x = receiving[Tier].entity
                xs = xs + [x]
                n[Tier] = n[Tier] + 1

        if selected(call_lift):
            pass

        if selected(sending):
            ### BEGIN SOLUTION
            Tier = xs[0].tier
            xs = xs[1:]
            n[Tier] = n[Tier] - 1
            ### END SOLUTION

            
# =================================
# Lift
# =================================
@process
def Lift(env, c_in, c_lift, c_out):
    while True: 
        ### BEGIN SOLUTION
        destination = yield env.execute(c_lift.receive())

        distance = dl * (destination+1)
        if distance <= vmaxl**2/al:
            duration = 2*math.sqrt(distance/al) + ll
        else:
            duration = distance/vmaxl +vmaxl/al + ll

        yield env.timeout(duration)
        x = yield env.execute(c_in.receive())
        yield env.timeout(duration)
        yield env.execute(c_out.send(x))
        ### END SOLUTION
        
# =================================
# Exit
# =================================
@process
def Exit(env, c_in):
    mphi = 0.0
    for i in range(1, number_of_orders + 1):
        x = yield env.execute(c_in.receive())
        mphi = (i - 1) / i * mphi + (env.now - x.entrytime) / i
        mthi = i/env.now
    return mphi, mthi 
            
        
# =================================
# GDV
# =================================
def GDV(env, c_out, Tier):
    a = Channel(env)  # for sending totes
    b = Channel(env)  # for sending totes
    G = Generator(env, a, Tier)
    D = Demand_Buffer(env, a,b)
    V = Vehicle(env, b, c_out)
        

# =================================
# Model
# =================================
def model():
    env = Environment()
    c = [Channel(env) for Tier in range(Level)] # a channel for each tier, each sending totes
    d = Channel(env)  # for sending totes
    e = Channel(env)  # for calling the lift
    f = Channel(env)  # for sending totes
    GDVs = [ GDV(env, c[Tier], Tier)  for Tier in range(Level) ] 
    B = Buffer(env, c, d, e)
    L = Lift(env, d, e, f)
    E = Exit(env, f)
    env.run(until=E)
    mph, mth = E.value
    print(f"--- Mean throughput = {mth:8.6f}; Mean flowtime = {mph:6.4f} ---")
    return mph, mth

# =================================
# Main
# =================================
mph, mth = model()

--- Mean throughput = 0.128661; Mean flowtime = 72.3825 ---


c. Verify if the throughput in your simulations matches with the start rate you determined. Verify that totes reach the exit from each tier. Also verify that totes are generated from each column.

Answer: ...



d. Run your simulation 30 times, and record for each run the resulting average throughput and average flow time.
Determine the mean and the standard deviation of both the average throughput and the average flow time for these 30 simulations. Finally, determine a 95% confidence interval for both the average throughput and the average flow time.

Answer: ...



## 6.10 Exercise 10: Effect of buffer capacity (10 points)
Via computer simulation analyze the impact of the buffer capacity on the throughput and flow time (choose values of `bc` as 1,2,3,200). For each setting, run your simulations 30 times and determine both mean and standard deviation of the resulting average throughput and average flow time for these 30 simulations, as well as 95% confidence intervals.

Answer: ...



## 6.11 Exercise 11: Looking for the best layout (30 points)
Via computer simulation consider 6 different scenarios (see the table below) that correspond to different layouts of the
storage facility with a total capacity of 500 totes with different number of tiers and columns.

| Scenario | 1 | 2 | 3 | 4| 5 | 6 |
| - | - | - | - | - | - | - |
| Level |  2 | 5 | 10 | 20 | 25 | 50 |
| Depth | 250 | 100 | 50 | 25 | 20 | 10 |

In order to obtain an answer to the questions below: for each scenario, run your simulations 30 times and determine both mean and standard deviation of the resulting average throughput and average flow time for these 30 simulations, as well as 95% confidence intervals.

a. For each scenario, determine by means of simulation the maximal throughput.

Answer: ...



b. Assume a required throughput of 6 totes per minute. Compare the resulting flow time for each feasible scenario.

Answer: ...



c. Based on your outcomes, select a layout that seems the best for you. If necessary, introduce other performance indicators and modify the code accordingly. The report on this step should contain an argument to select the best layout.

Answer: ...



## References
[1] G. Marchet, M. Melanci, S. Perotti and E. Tappia, "Analytical model to estimate performance of autonomous vehicle storage and retrieval systems for product totes", International Journal of Production Research, vol. 50(24), 7134-7148, 2012.